In [1]:
import numpy as np
import pandas as pd
from collections import defaultdict
import operator
import time, datetime
from utils import *

from IPython.display import display, HTML
# display(HTML("<style>.container { width:100% !important; }</style>"))

In [2]:
# modified 0330

# 1. statistics overview

In [4]:
bath_path = '/mnt/qb/work/mlcolab/hzhou52/kt/duolingo/learning_traces.csv'
log = pd.read_csv(bath_path, encoding = "utf-8",low_memory=False)

print('The columns of log are ', log.columns)
print('The length of log is {}'.format(len(log)))

print('###########################################')

print(count_unique(log, log.columns))

The columns of log are  Index(['p_recall', 'timestamp', 'delta', 'user_id', 'learning_language',
       'ui_language', 'lexeme_id', 'lexeme_string', 'history_seen',
       'history_correct', 'session_seen', 'session_correct'],
      dtype='object')
The length of log is 12854226
###########################################
Number of unique values in p_recall: 77
Number of unique values in timestamp: 574814
Number of unique values in delta: 1593664
Number of unique values in user_id: 115222
Number of unique values in learning_language: 6
Number of unique values in ui_language: 4
Number of unique values in lexeme_id: 19279
Number of unique values in lexeme_string: 18781
Number of unique values in history_seen: 5897
Number of unique values in history_correct: 4785
Number of unique values in session_seen: 20
Number of unique values in session_correct: 21
None


In [6]:
for col in log.columns:
    print(col, log[col][0:5])

p_recall 0    1.0
1    0.5
2    1.0
3    0.5
4    1.0
Name: p_recall, dtype: float64
timestamp 0    1362076081
1    1362076081
2    1362076081
3    1362076081
4    1362076081
Name: timestamp, dtype: int64
delta 0    27649635
1    27649635
2    27649635
3    27649635
4    27649635
Name: delta, dtype: int64
user_id 0    u:FO
1    u:FO
2    u:FO
3    u:FO
4    u:FO
Name: user_id, dtype: object
learning_language 0    de
1    de
2    de
3    de
4    de
Name: learning_language, dtype: object
ui_language 0    en
1    en
2    en
3    en
4    en
Name: ui_language, dtype: object
lexeme_id 0    76390c1350a8dac31186187e2fe1e178
1    7dfd7086f3671685e2cf1c1da72796d7
2    35a54c25a2cda8127343f6a82e6f6b7d
3    0cf63ffe3dda158bc3dbd55682b355ae
4    84920990d78044db53c1b012f5bf9ab5
Name: lexeme_id, dtype: object
lexeme_string 0    lernt/lernen<vblex><pri><p3><sg>
1       die/die<det><def><f><sg><nom>
2            mann/mann<n><m><sg><nom>
3            frau/frau<n><f><sg><nom>
4      das/das<det><def><nt

In [9]:
check_nan(log)

Number of NaN values in column p_recall: 0
Number of NaN values in column timestamp: 0
Number of NaN values in column delta: 0
Number of NaN values in column user_id: 0
Number of NaN values in column learning_language: 0
Number of NaN values in column ui_language: 0
Number of NaN values in column lexeme_id: 0
Number of NaN values in column lexeme_string: 0
Number of NaN values in column history_seen: 0
Number of NaN values in column history_correct: 0
Number of NaN values in column session_seen: 0
Number of NaN values in column session_correct: 0


In [7]:
interested_col = [
    'user_id', 'lexeme_id', 'lexeme_id','lexeme_string', 'timestamp', 'p_recall'
]
invert_col = [
    'user_id', 'problem_id', 'skill_id', 'skill_text', 'timestamp', 'correct', 
]

In [8]:
log.head()

p_recall   timestamp     delta user_id learning_language ui_language  \
0       1.0  1362076081  27649635    u:FO                de          en   
1       0.5  1362076081  27649635    u:FO                de          en   
2       1.0  1362076081  27649635    u:FO                de          en   
3       0.5  1362076081  27649635    u:FO                de          en   
4       1.0  1362076081  27649635    u:FO                de          en   

                          lexeme_id                     lexeme_string  \
0  76390c1350a8dac31186187e2fe1e178  lernt/lernen<vblex><pri><p3><sg>   
1  7dfd7086f3671685e2cf1c1da72796d7     die/die<det><def><f><sg><nom>   
2  35a54c25a2cda8127343f6a82e6f6b7d          mann/mann<n><m><sg><nom>   
3  0cf63ffe3dda158bc3dbd55682b355ae          frau/frau<n><f><sg><nom>   
4  84920990d78044db53c1b012f5bf9ab5    das/das<det><def><nt><sg><nom>   

   history_seen  history_correct  session_seen  session_correct  
0             6                4             2                2  
1             4                4             2                1  
2             5                4             1                1  
3             6                5             2                1  
4             4                4             1                1

In [7]:
check_nan(log)
count_unique(log, ['user_id', 'learning_language', 'lexeme_id'])
print('total number of logs: ', len(log))

number of NaN in column p_recall: 0
number of NaN in column timestamp: 0
number of NaN in column delta: 0
number of NaN in column user_id: 0
number of NaN in column learning_language: 0
number of NaN in column ui_language: 0
number of NaN in column lexeme_id: 0
number of NaN in column lexeme_string: 0
number of NaN in column history_seen: 0
number of NaN in column history_correct: 0
number of NaN in column session_seen: 0
number of NaN in column session_correct: 0
number of unique value in user_id: 115222
number of unique value in learning_language: 6
number of unique value in lexeme_id: 19279
total number of logs:  12854226


In [13]:
log['p_recall'].mean()

0.8961055619872841

In [11]:
log['p_recall'].unique()

array([1.        , 0.5       , 0.75      , 0.88888889, 0.8       ,
       0.        , 0.66666667, 0.4       , 0.33333333, 0.875     ,
       0.85714286, 0.83333333, 0.92307692, 0.90909091, 0.6       ,
       0.9       , 0.9375    , 0.93333333, 0.92857143, 0.77777778,
       0.71428571, 0.81818182, 0.72727273, 0.85      , 0.25      ,
       0.57142857, 0.84615385, 0.86666667, 0.91666667, 0.625     ,
       0.89473684, 0.7       , 0.94736842, 0.8125    , 0.78571429,
       0.95      , 0.94117647, 0.63636364, 0.76470588, 0.76923077,
       0.16666667, 0.42857143, 0.73333333, 0.28571429, 0.2       ,
       0.69230769, 0.55555556, 0.73684211, 0.64285714, 0.84210526,
       0.44444444, 0.94444444, 0.41176471, 0.88235294, 0.53846154,
       0.6875    , 0.82352941, 0.78947368, 0.46666667, 0.68421053,
       0.58333333, 0.27272727, 0.61538462, 0.45454545, 0.1       ,
       0.14285714, 0.11111111, 0.3       , 0.36363636, 0.47058824,
       0.375     , 0.54545455, 0.21428571, 0.18181818, 0.125  

# 2. remove learner logs with threshold

In [24]:
user_index = 'user_id'
skill_index = 'lexeme_id'

In [16]:
remove_thres = [50, 100, 150, 200]

bath_path = '/mnt/qb/work/mlcolab/hzhou52/kt/duolingo/learning_traces.csv'
log = pd.read_csv(bath_path, encoding = "utf-8",low_memory=False)

for thres in remove_thres:
    print('remove threshold is {}'.format(thres))
    log = log[~log[skill_index].isna()]
    log = remove_log(log, user_index, num=thres)
    count_unique(log, [user_index, skill_index])
    print(len(log))

remove threshold is 50
Number of unique values in user_id: 48454
Number of unique values in lexeme_id: 19203
11730745
remove threshold is 100
Number of unique values in user_id: 31606
Number of unique values in lexeme_id: 19112
10528990
remove threshold is 150
Number of unique values in user_id: 22249
Number of unique values in lexeme_id: 18997
9383789
remove threshold is 200
Number of unique values in user_id: 16838
Number of unique values in lexeme_id: 18889
8449234


In [22]:
remove_thres = [50, 100, 150, 200]

bath_path = '/mnt/qb/work/mlcolab/hzhou52/kt/duolingo/learning_traces.csv'
log = pd.read_csv(bath_path, encoding = "utf-8",low_memory=False)

In [26]:
for thres in remove_thres:
    print(f'Remove threshold is {thres}')

    # Remove rows with NaN skill_id and users who appear less than thres times
    # log = log[~log[skill_index.isna()]]
    log = remove_log(log, user_index, num=thres)

    # Create new DataFrame with desired columns
    df = log[interested_col].copy()
    df.columns = invert_col
    
    # Re-index columns
    df['skill_id'] = pd.Categorical(df['skill_id'], categories=df['skill_id'].unique()).codes
    df['problem_id'] = pd.Categorical(df['problem_id'], categories=df['problem_id'].unique()).codes
    df['user_id'] = pd.Categorical(df['user_id'], categories=df['user_id'].unique()).codes
    df = df.astype({'timestamp': np.float64, 'correct': np.float64})
    df = df.astype({'problem_id': np.int64, 'user_id': np.int64, 'skill_id': np.int64})
    
    # Save cleaned DataFrame to a CSV file
    df.to_csv(f'/mnt/qb/work/mlcolab/hzhou52/kt/duolingo/multi_skill/interactions_{thres}.csv', sep='\t', index=False)

    print(f'Remove threshold {thres} is done!')
    print(count_unique(df, df.columns.tolist()))
    print(f'Length of DataFrame: {len(df)}')

Remove threshold is 50
Remove threshold 50 is done!
Number of unique values in user_id: 48454
Number of unique values in problem_id: 19203
Number of unique values in skill_id: 19203
Number of unique values in skill_text: 18707
Number of unique values in timestamp: 518306
Number of unique values in correct: 75
None
Length of DataFrame: 11730745
Remove threshold is 100
Remove threshold 100 is done!
Number of unique values in user_id: 31606
Number of unique values in problem_id: 19112
Number of unique values in skill_id: 19112
Number of unique values in skill_text: 18627
Number of unique values in timestamp: 471697
Number of unique values in correct: 71
None
Length of DataFrame: 10528990
Remove threshold is 150
Remove threshold 150 is done!
Number of unique values in user_id: 22249
Number of unique values in problem_id: 18997
Number of unique values in skill_id: 18997
Number of unique values in skill_text: 18517
Number of unique values in timestamp: 426599
Number of unique values in corre

# 3. extract single learner 

In [28]:
remove_thres = [50, 100, 150, 200]

bath_path = '/mnt/qb/work/mlcolab/hzhou52/kt/duolingo/learning_traces.csv'
log = pd.read_csv(bath_path, encoding = "utf-8",low_memory=False)

users = []
users_log = log.groupby([user_index, skill_index]).size().reset_index(name='count')

for thres in remove_thres:
    users.append(users_log[users_log['count']>thres])

In [44]:
######################################## single_user_single_exercise
from tqdm import tqdm
useful_log = log[interested_col]
remove_thres = [50, 100, 150, 200]

skill_index = 'lexeme_id'

users_logs_threshold = []
for i in range(len(remove_thres)):
    thres = remove_thres[i]
    users_with_threshold = users[i]
    
    single_skill = {col: [] for col in interested_col}

    sk_dfs = []
    print('With threshold {} there are {} logs'.format(thres, len(users_with_threshold)))
    for j in tqdm(range(len(users_with_threshold))):
        id = users_with_threshold[user_index].iloc[j]
        ex = users_with_threshold[skill_index].iloc[j]

        single_user_exercise = useful_log.loc[(useful_log[user_index] == id) & (useful_log[skill_index] == ex)]
        single_user_exercise = single_user_exercise.sort_values('timestamp')[:thres]

        sk_dfs.append(single_user_exercise)
    users_logs_threshold.append(sk_dfs)

With threshold 50 there are 1754 logs


100%|██████████| 1754/1754 [39:30<00:00,  1.35s/it]


With threshold 100 there are 260 logs


100%|██████████| 260/260 [05:50<00:00,  1.35s/it]


With threshold 150 there are 83 logs


100%|██████████| 83/83 [01:52<00:00,  1.35s/it]


With threshold 200 there are 16 logs


100%|██████████| 16/16 [00:21<00:00,  1.35s/it]


In [45]:
users_logs_threshold[0]

[         user_id                         lexeme_id        lexeme_string  \
 1438919     u:-b  1e1f8d730c4ba99ad2873a7608324cf6  my/my<det><pos><sp>   
 1439893     u:-b  1e1f8d730c4ba99ad2873a7608324cf6  my/my<det><pos><sp>   
 1443117     u:-b  1e1f8d730c4ba99ad2873a7608324cf6  my/my<det><pos><sp>   
 1446657     u:-b  1e1f8d730c4ba99ad2873a7608324cf6  my/my<det><pos><sp>   
 1536524     u:-b  1e1f8d730c4ba99ad2873a7608324cf6  my/my<det><pos><sp>   
 2384828     u:-b  1e1f8d730c4ba99ad2873a7608324cf6  my/my<det><pos><sp>   
 2387586     u:-b  1e1f8d730c4ba99ad2873a7608324cf6  my/my<det><pos><sp>   
 2454576     u:-b  1e1f8d730c4ba99ad2873a7608324cf6  my/my<det><pos><sp>   
 3394879     u:-b  1e1f8d730c4ba99ad2873a7608324cf6  my/my<det><pos><sp>   
 3404807     u:-b  1e1f8d730c4ba99ad2873a7608324cf6  my/my<det><pos><sp>   
 3421446     u:-b  1e1f8d730c4ba99ad2873a7608324cf6  my/my<det><pos><sp>   
 3426031     u:-b  1e1f8d730c4ba99ad2873a7608324cf6  my/my<det><pos><sp>   
 3428727    

In [48]:
interested_col = [
    'user_id', 'lexeme_id', 'lexeme_string', 'timestamp', 'p_recall'
]

invert_col = [
    'user_id', 'problem_id', 'skill_text', 'timestamp', 'correct', 
]
for i in range(len(users_logs_threshold)):
    test = users_logs_threshold[i]
    test = pd.concat(test, axis=0)
    thres = remove_thres[i]

    test.columns = invert_col
    new_id = [[i] * thres for i in range(len(users_logs_threshold[i]))]
    new_user_id = [item for sublist in new_id for item in sublist]
    test['user_id'] = new_user_id

    test['skill_id'] = pd.Categorical(test['skill_text'], categories=test['skill_text'].unique()).codes
    test['problem_id'] = pd.Categorical(test['problem_id'], categories=test['problem_id'].unique()).codes

    # Re-index columns
    test = test.astype({'timestamp': np.float64, 'correct': np.float64})
    test = test.astype({'problem_id': np.int64, 'user_id': np.int64, 'skill_id': np.int64})

    # Save
    bath_path = '/mnt/qb/work/mlcolab/hzhou52/kt/duolingo/single_skill/'
    test.to_csv(bath_path+'interactions_{}.csv'.format(thres), sep='\t', index=False)